# Estudo prático da estrutura das redes neurais artificiais - Classificação multiclasse

#### Sabrina Otoni da Silva - 2023

In [ ]:
import pandas as pd
import numpy as np

import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout
from tensorflow.keras import backend as k
from tensorflow.keras.utils import to_categorical

from scikeras.wrappers import KerasClassifier

from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.metrics import confusion_matrix

In [2]:
base = pd.read_csv('iris.csv')
previsores = base.iloc[:, 0:4].values
classe = base.iloc[:, 4].values

In [3]:
labelencoder = LabelEncoder()
classe = labelencoder.fit_transform(classe)
classe_dummy = to_categorical(classe)

In [9]:
previsores_treinamento, previsores_teste, classe_treinamento, classe_teste = train_test_split(previsores, classe_dummy, test_size=0.25)

classificador = Sequential([
               tf.keras.layers.Dense(units=4, activation = 'relu', input_dim=4),
               tf.keras.layers.Dense(units=4, activation = 'relu'),
               tf.keras.layers.Dense(units=3, activation = 'softmax')])

classificador.compile(optimizer = 'adam', loss = 'categorical_crossentropy',
                      metrics = ['categorical_accuracy'])

classificador.fit(previsores_treinamento, classe_treinamento, batch_size = 10,
                  epochs = 1000)

Epoch 1/1000
12/12 [==============================] - 1s 3ms/step - loss: 1.3210 - categorical_accuracy: 0.0000e+00
Epoch 2/1000
12/12 [==============================] - 0s 2ms/step - loss: 1.2051 - categorical_accuracy: 0.0000e+00
Epoch 3/1000
12/12 [==============================] - 0s 2ms/step - loss: 1.1341 - categorical_accuracy: 0.0982
Epoch 4/1000
12/12 [==============================] - 0s 2ms/step - loss: 1.1074 - categorical_accuracy: 0.2768
Epoch 5/1000
12/12 [==============================] - 0s 2ms/step - loss: 1.1017 - categorical_accuracy: 0.3214
Epoch 6/1000
12/12 [==============================] - 0s 1ms/step - loss: 1.1006 - categorical_accuracy: 0.3304
Epoch 7/1000
12/12 [==============================] - 0s 3ms/step - loss: 1.0998 - categorical_accuracy: 0.3304
Epoch 8/1000
12/12 [==============================] - 0s 1ms/step - loss: 1.0995 - categorical_accuracy: 0.3304
Epoch 9/1000
12/12 [==============================] - 0s 3ms/step - loss: 1.0995 - categorical_a

In [10]:
classificador.evaluate(previsores_teste, classe_teste)

2/2 [==============================] - 0s 15ms/step - loss: 1.1065 - categorical_accuracy: 0.2895


[1.106532096862793, 0.28947368264198303]

In [11]:
previsoes = classificador.predict(previsores_teste)
previsoes = (previsoes > 0.5)

classe_teste2 = [np.argmax(t) for t in classe_teste]
previsoes2 = [np.argmax(t) for t in previsoes]

confusion_matrix(previsoes2, classe_teste2)

2/2 [==============================] - 0s 3ms/step


array([[11, 12, 15],
       [ 0,  0,  0],
       [ 0,  0,  0]], dtype=int64)

In [ ]:
def criar_rede():
    k.clear_session()
    classificador = Sequential([
    tf.keras.layers.Dense(units=4, activation = 'relu', input_dim=4),
    tf.keras.layers.Dense(units=4, activation = 'relu'),
    tf.keras.layers.Dense(units=3, activation = 'softmax')])
    classificador.compile(optimizer = 'adam', loss = 'categorical_crossentropy',
                          metrics = ['categorical_accuracy'])
    return classificador

classificador = KerasClassifier(build_fn = criar_rede,
                                epochs = 1000,
                                batch_size = 10)

resultados = cross_val_score(estimator = classificador,
                             X = previsores, y = classe_dummy,
                             cv = 10, scoring = 'accuracy')

print(resultados.mean())
print(resultados.std())

In [12]:
def criar_rede2(optimizer='adam'):
    k.clear_session()
    classificador = Sequential()
    classificador.add(Dense(units = 4, activation = 'relu', 
                            kernel_initializer = 'random_uniform', input_dim = 4))
    classificador.add(Dropout(0.2))
    classificador.add(Dense(units = 4, activation = 'relu', 
                            kernel_initializer = 'random_uniform'))
    classificador.add(Dropout(0.2))
    classificador.add(Dense(units = 3, activation = 'softmax'))
    classificador.compile(optimizer = optimizer, 
                          loss = 'sparse_categorical_crossentropy', 
                          metrics = ['accuracy'])
    return classificador

classificador = KerasClassifier(build_fn = criar_rede2)

parametros = {'batch_size': [10, 30],
              'epochs': [2000, 3000],
              'optimizer': ['adam', 'sgd']}

grid_search = GridSearchCV(estimator = classificador,
                           param_grid = parametros,                           
                           cv = 2)

grid_search = grid_search.fit(previsores, classe)
melhores_parametros = grid_search.best_params_
melhor_precisao = grid_search.best_score_

Epoch 1/2000


c:\Users\012728631\AppData\Local\anaconda3\Lib\site-packages\scikeras\wrappers.py:915: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)


8/8 [==============================] - 1s 6ms/step - loss: 1.0972 - accuracy: 0.4267
Epoch 2/2000
8/8 [==============================] - 0s 3ms/step - loss: 1.0970 - accuracy: 0.3467
Epoch 3/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0942 - accuracy: 0.3867
Epoch 4/2000
8/8 [==============================] - 0s 1ms/step - loss: 1.0949 - accuracy: 0.3600
Epoch 5/2000
8/8 [==============================] - 0s 1ms/step - loss: 1.0953 - accuracy: 0.3200
Epoch 6/2000
8/8 [==============================] - 0s 1ms/step - loss: 1.0933 - accuracy: 0.3200
Epoch 7/2000
8/8 [==============================] - 0s 1ms/step - loss: 1.0906 - accuracy: 0.3333
Epoch 8/2000
8/8 [==============================] - 0s 1ms/step - loss: 1.0915 - accuracy: 0.3067
Epoch 9/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0827 - accuracy: 0.3467
Epoch 10/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0836 - accuracy: 0.3067
Epoch 11/2000
8/8 [=============

c:\Users\012728631\AppData\Local\anaconda3\Lib\site-packages\scikeras\wrappers.py:915: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)


8/8 [==============================] - 0s 2ms/step - loss: 1.0989 - accuracy: 0.3200
Epoch 2/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0983 - accuracy: 0.4933
Epoch 3/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0980 - accuracy: 0.5333
Epoch 4/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0972 - accuracy: 0.5600
Epoch 5/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0971 - accuracy: 0.5067
Epoch 6/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0970 - accuracy: 0.4933
Epoch 7/2000
8/8 [==============================] - 0s 5ms/step - loss: 1.0960 - accuracy: 0.5733
Epoch 8/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0954 - accuracy: 0.5467
Epoch 9/2000
8/8 [==============================] - 0s 1ms/step - loss: 1.0943 - accuracy: 0.4933
Epoch 10/2000
8/8 [==============================] - 0s 2ms/step - loss: 1.0935 - accuracy: 0.5467
Epoch 11/2000
8/8 [=============

...

Epoch 1/3000
3/3 [==============================] - 1s 4ms/step - loss: 1.0976 - accuracy: 0.3467
Epoch 2/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0970 - accuracy: 0.3467
Epoch 3/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0965 - accuracy: 0.3467
Epoch 4/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0960 - accuracy: 0.3333
Epoch 5/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0929 - accuracy: 0.3867
Epoch 6/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0927 - accuracy: 0.3600
Epoch 7/3000
3/3 [==============================] - 0s 2ms/step - loss: 1.0936 - accuracy: 0.3200
Epoch 8/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0951 - accuracy: 0.3467
Epoch 9/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0924 - accuracy: 0.3600
Epoch 10/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0911 - accuracy: 0.3467
Epoch 11/3000
3/3 [

c:\Users\012728631\AppData\Local\anaconda3\Lib\site-packages\scikeras\wrappers.py:915: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)


3/3 [==============================] - 1s 5ms/step - loss: 1.0983 - accuracy: 0.2400
Epoch 2/3000
3/3 [==============================] - 0s 4ms/step - loss: 1.0959 - accuracy: 0.5067
Epoch 3/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0965 - accuracy: 0.4400
Epoch 4/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0956 - accuracy: 0.4800
Epoch 5/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0936 - accuracy: 0.5200
Epoch 6/3000
3/3 [==============================] - 0s 4ms/step - loss: 1.0930 - accuracy: 0.4933
Epoch 7/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0935 - accuracy: 0.4533
Epoch 8/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0917 - accuracy: 0.5067
Epoch 9/3000
3/3 [==============================] - 0s 8ms/step - loss: 1.0907 - accuracy: 0.5200
Epoch 10/3000
3/3 [==============================] - 0s 3ms/step - loss: 1.0888 - accuracy: 0.5333
Epoch 11/3000
3/3 [=============

c:\Users\012728631\AppData\Local\anaconda3\Lib\site-packages\scikeras\wrappers.py:915: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)


5/5 [==============================] - 1s 3ms/step - loss: 1.0975 - accuracy: 0.3733
Epoch 2/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0975 - accuracy: 0.3800
Epoch 3/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0964 - accuracy: 0.4067
Epoch 4/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0953 - accuracy: 0.4400
Epoch 5/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0967 - accuracy: 0.3267
Epoch 6/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0955 - accuracy: 0.3333
Epoch 7/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0931 - accuracy: 0.3867
Epoch 8/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0913 - accuracy: 0.4133
Epoch 9/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0898 - accuracy: 0.3933
Epoch 10/2000
5/5 [==============================] - 0s 2ms/step - loss: 1.0876 - accuracy: 0.4267
Epoch 11/2000
5/5 [=============

In [14]:
melhores_parametros

{'batch_size': 30, 'epochs': 2000, 'optimizer': 'sgd'}

In [15]:
melhor_precisao

0.9733333333333334